In [ ]:
pip install contractions

     |████████████████████████████████| 266kB 7.8MB/s 
     |████████████████████████████████| 327kB 19.0MB/s 
  Created wheel for pyahocorasick: filename=pyahocorasick-1.4.2-cp37-cp37m-linux_x86_64.whl size=85392 sha256=3a0b431fba1e4051734f10e9e25679e9f06453be63f9afbfbe6bd78db47a3a95
  Stored in directory: /root/.cache/pip/wheels/3a/03/34/77e3ece0bba8b86bfac88a79f923b36d805cad63caeba38842
Successfully built pyahocorasick


In [ ]:
import pickle
import nltk
nltk.download('punkt')
nltk.download('wordnet')
import re
from nltk.tokenize import sent_tokenize
from nltk.tokenize import word_tokenize
nltk.download ('stopwords')
from nltk.corpus import stopwords 
import glob
import ntpath
import contractions
from google.colab import drive
from nltk.stem import WordNetLemmatizer 

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


In [ ]:
import os
drive.mount('/content/drive')
files_list = glob.glob("drive/My Drive/stories/stories/" + '**/*', recursive=True)   
files_list.remove("drive/My Drive/stories/stories/SRE")

Mounted at /content/drive


Preprocessing

In [ ]:
#Function for preprocessing
def pre_processing(file_path, temp):
  tokens=[]
  if(temp==0):                                         ## parameter is a file
    rfile = open(file_path,'r',errors = 'ignore')
    read_file = rfile.read().replace('\n', ' ')
  else:                                               ## paramter is a query
    read_file=file_path   
  clean_string = re.sub(r'[\!@#$%^&\*()\_+={}\:\;<>\?/\|\,\-/"\']'," ",read_file)
  clean_string = re.sub('\s+', ' ', clean_string)
  clean_string = re.sub('^\s+', '', clean_string)
  clean_string = re.sub("([\-]{1,2})", " ",clean_string)
  clean_string = re.sub('([>|\-=+~]+)', ' ', clean_string)
  clean_string=re.sub("([\.\!]{2})", " ",clean_string)
  clean_string=re.sub("[^a-zA-Z\s\n]", " ",clean_string)  
  read_file = re.sub(r"(.)\1{2}","",clean_string)                  

  #convert to lowercase
  read_file = read_file.lower() 

  #Tokenisation
  sent_tokens = sent_tokenize(read_file)   
  strings = ''  
  
  #Tokenize sentences into words
  for w in sent_tokens:
    word = w.split(' ')
    clean_string = ' '.join(word)          

    #Remove stopwords from tokens
    clean_word = clean_string.split(' ')
    stop_words = set(stopwords.words('english'))
    for x in clean_word:
      if x not in stop_words and len(x)>1:
        tokens.append(x)
  return tokens

Positional Index

In [ ]:
doc=1
pos_index={}                      # dictionary of positional indexing
file_word={}                     # mapping of file number with file name
for file_path in files_list:
  doc_id = ntpath.basename(file_path) 
  file_word[doc]=doc_id
  tokens=pre_processing(file_path,0)        #preprocessing of file

  for pos, token in enumerate(tokens):
    if token not in pos_index:
      pos_index[token]=[1, {}]
      pos_index[token][1][doc]=[pos]
    else:
      if doc not in pos_index[token][1]:
        pos_index[token][0]+=1
        pos_index[token][1][doc]=[]
      pos_index[token][1][doc].append(pos)                    #      if(pos not in pos_index[token][1][doc]):
  doc=doc+1

In [ ]:
pos_index

{'adventures': [43,
  {1: [0, 4, 880],
   2: [0],
   4: [0, 468],
   7: [0, 4, 1589],
   9: [15],
   11: [61],
   15: [0, 4, 1089, 1126],
   16: [0, 4],
   18: [130],
   19: [0],
   20: [0, 250],
   21: [1977, 2094],
   25: [1],
   57: [0],
   69: [85],
   84: [5, 796, 1752, 3106],
   86: [1],
   132: [16837],
   144: [3364],
   221: [1201, 17993, 31107, 42469],
   225: [15569, 15614, 24063, 24494],
   233: [867],
   235: [6453, 11172, 11798],
   236: [1],
   241: [522,
    654,
    798,
    1212,
    1247,
    1277,
    1382,
    1592,
    1632,
    1862,
    1898,
    2269,
    2589,
    2594,
    2599,
    2604,
    2999,
    3004,
    3028,
    3032,
    3112],
   246: [263, 7688],
   283: [28],
   296: [678],
   307: [251],
   325: [1422, 1526, 1567],
   362: [9301],
   365: [4271, 11787],
   370: [3371],
   392: [1780, 3483],
   398: [3711],
   404: [1228, 1248],
   407: [1184, 3247],
   410: [913],
   433: [14729],
   441: [3602],
   459: [9, 1738, 1818],
   465: [2198],
   467:

Storing the positinal Index and File mapping

In [ ]:
#Saving the positional Index
out=open("/content/drive/My Drive/positional_index", 'wb')
pickle.dump(pos_index,out)
out.close()

# Saving the file mapping
out=open("/content/drive/My Drive/file_map", 'wb')
pickle.dump(file_word,out)
out.close()

Loading the pickle file


In [ ]:
#Loadind positional Indexes
inp=open("/content/drive/My Drive/positional_index", 'rb')
pos_index=pickle.load(inp)
inp.close()

#Loading file mapping
inp=open("/content/drive/My Drive/file_map", 'rb')
file_word=pickle.load(inp)
inp.close()

Query


In [ ]:
def intersect(list1, list2, k):
  document=[]
  for doc in list1:
    if(doc in list2):
      pos_1=list1[doc]
      pos_2=list2[doc]

      for i in pos_1:
        for j in pos_2:
          if ((j-i)==k):
            if(doc not in document):
              document.append(doc)
            break
  return document

In [ ]:
query=input("Enter query ")
query_token = pre_processing(query,1)
print(query_token)

tot_documents=[]
if(len(query_token)==1):
  if(query_token[0] in pos_index):
    for a in pos_index[query_token[0]][1]:
      tot_documents.append(a)

else:
  matched=[]
  for i in range(len(query_token)):
    j=i+1
    list1=[]
    if query_token[i] in pos_index:
      list1=pos_index[query_token[i]]

    while(j<len(query_token)):
      list2=[] 
      if query_token[j] in pos_index:
        list2=(pos_index[query_token[j]])
      if(list1==[] and list2==[]):
        matched.append(intersect([], [], j-i))
      elif(list1==[]):
        matched.append(intersect([], list2[1], j-i))
      elif(list2==[]):
        matched.append(intersect(list1[1], [], j-i))
      else:
        matched.append(intersect(list1[1], list2[1], j-i))
      j=j+1
  
  for i in matched:
     for j in i:
       if j not in tot_documents:
         tot_documents.append(j)
print("total number of documents are ", len(tot_documents))
print("The documents are ")
for i in tot_documents:
  print(file_word[i])

Enter query two day
['two', 'day']
total number of documents are  1
The documents are 
history5.txt
